In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import io
import requests
import math as m
from scipy.optimize import curve_fit
import scipy.stats
from scipy import integrate

%pylab notebook

# 0. Úhel

In [ ]:
l1 = 33
l2 = 27
h = 9.42
alpha = np.linspace(-25,25,401)
dist = np.linspace(15,45,401)

def f_distance(a):
    return np.sqrt(l1**2 - (l2*np.cos(a) - h)**2) + l2*np.sin(a)

def f_alpha(d,a,b,c):
    return a*d**2+b*d+c

popt_dist, pcov_dist = curve_fit(f_alpha, f_distance(np.pi*alpha/180), alpha, p0 = [1,1,1])#, sigma=I_lp_s )
print(popt_dist)

zero_dist = f_distance(0)

def get_alpha(dist):
    return popt_dist[0]*dist**2 + popt_dist[1]*dist + popt_dist[2]

fig, ax = plt.subplots(figsize=(6, 4))
#plt.plot(f_distance(np.pi*alpha/180), alpha,"r-")
#plt.plot(alpha, f_distance(np.pi*alpha/180),"b-")
plt.plot(dist - zero_dist, get_alpha(dist),"g-")
plt.xlabel("d [mm]")
plt.ylabel("$\\alpha$ [DEG]")
plt.show()

# 1. Data

In [ ]:
def get_data(shot, ch="lp"):
    """
    Stáhne data z http://golem.fjfi.cvut.cz/shots/0/, 
    bere parametr shot: číslo výboje,
    ch: kanál: lp - Langmuir, bp - Ball-pen, uloop, btor, irog
    a vrací panda tabulku index, t: čas, U: měřený signál
    """
    url = "http://golem.fjfi.cvut.cz/shots/"+str(shot)+"/Diagnostics/"+ch+".csv"
    s = requests.get(url).content
    data = pd.read_csv(io.StringIO(s.decode('utf-8')), sep=',', header=0, names=["t","U"])
    return data

In [ ]:
def get_data_uloop(shot):
    calibration_uloop = 5.23*0.1966
    data_uloop = get_data(shot,ch="BasicDiagnostics/U_Loop")
    data_uloop["U"] *= calibration_uloop
    return data_uloop
    
def get_data_btor(shot):
    calibration_btor = 69.3
    data = get_data(shot,ch="BasicDiagnostics/U_BtCoil")
    zerotime = int(0.03*len(data))
    data_for_int = data["U"] - np.mean(data["U"][0:zerotime])
    data_int = integrate.cumtrapz(data_for_int, data["t"], initial=0)
    data_calibrated = calibration_btor*data_int
    data_btor = pd.DataFrame({'t': data["t"], 'U': data_calibrated})
    return data_btor

def get_data_irog(shot):
    calibration_irog = 1.42*3320000/0.8765
    resistance_ch = 0.0097/0.915
    data_irog = get_data(shot,ch="BasicDiagnostics/U_RogCoil")
    zerotime = int(0.05*len(data_irog))
    data_for_int_irog = data_irog["U"] - np.mean(data_irog["U"][0:zerotime])
    data_int_irog = integrate.cumtrapz(data_for_int_irog, data_irog["t"], initial=0)
    data_irog_calibrated = data_int_irog * calibration_irog
    data_uloop = get_data_uloop(shot)
    data_irog_calibrated = -1*data_irog_calibrated - data_uloop["U"]/resistance_ch
    data_irog = pd.DataFrame({'t': data_irog["t"], 'U': data_irog_calibrated})
    return data_irog

In [ ]:
shot_no = 35957
shotNo = shot_no

fig, ax = plt.subplots(figsize=(8, 12))
plt.title("Shot #"+str(shotNo))

plt.subplot(711) #irog

plt.plot(get_data_irog(shotNo)["t"], get_data_irog(shotNo)["U"], "b-",label="Plasma current", linewidth=0.4)
plt.legend(loc=1)
plt.grid()
plt.xlabel("t [s]")
plt.ylabel("$I_{plasma}$ [A]")

plt.subplot(712) #uloop

plt.plot(get_data_uloop(shotNo)["t"], get_data_uloop(shotNo)["U"], "b-",label="Loop voltage", linewidth=0.2)
plt.legend(loc=1)
plt.grid()
plt.xlabel("t [s]")
plt.ylabel("$U_{loop}$ [V]")


plt.subplot(713) #btor

plt.plot(get_data_btor(shotNo)["t"], get_data_btor(shotNo)["U"], "b-",label="Tor. mag. field", linewidth=0.4)
plt.legend(loc=1)
plt.grid()
plt.xlabel("t [s]")
plt.ylabel("$B_{T}$ [T]")


plt.subplot(714) #lp

data_lp = get_data(shotNo, ch="RailProbe/I_sat_LP")
plt.plot(data_lp["t"], data_lp["U"], "b-",label="Langmuir probe", linewidth=0.5)
plt.legend(loc=1)
plt.grid()
plt.ylim([-1,7])
plt.xlabel("t [s]")
plt.ylabel("$U_{lp}$ [V]")

plt.subplot(715) #rp

data_rp = get_data(shotNo, ch="RailProbe/I_sat_RP")
plt.plot(data_rp["t"], data_rp["U"], "b-",label="Rail probe", linewidth=0.5)
plt.legend(loc=1)
plt.grid()
plt.ylim([-1,7])
plt.xlabel("t [s]")
plt.ylabel("$U_{rp}$ [V]")


plt.subplot(716) #lp

data_bp = get_data(shotNo, ch="RailProbe/I_sat_LP")
plt.plot(data_bp["t"], data_bp["U"], "b-",label="Ball-pen probe", linewidth=0.8)
plt.legend(loc=1)
plt.grid()
plt.xlabel("t [s]")
plt.ylabel("$U_{bpp}$ [V]")
"""
plt.subplot(717) #bp

data_U = [0,0]#get_data(shotNo, ch="RailProbe/I_sat_LP")
plt.plot(data_U["t"], data_U["U"], "b-",label="Napětí na sondách", linewidth=0.8)
plt.legend(loc=1)
plt.grid()
plt.xlabel("t [s]")
plt.ylabel("$U_{bpp}$ [V]")
"""
plt.savefig('icon-fig.png')
plt.show()
